In [53]:
!pip install pyserini

In [54]:
import json
import pandas as pd
from tqdm import tqdm

In [55]:
data = pd.read_csv('Pubmed 220 Train 2022-01-21.txt', sep="\n#", header=None)


<ipython-input-55-27e163538fd8>:1: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  data = pd.read_csv('Pubmed 220 Train 2022-01-21.txt', sep="\n#", header=None)


In [56]:
data.head(13)

0
0                                         ###24491034
1   BACKGROUND\tThe emergence of HIV as a chronic ...
2   BACKGROUND\tThis paper describes the design an...
3   METHODS\tThis study is designed as a randomise...
4   METHODS\tThe intervention group will participa...
5   METHODS\tThe program is based on self-efficacy...
6   METHODS\tParticipants will access the program ...
7   METHODS\tPrimary outcomes are domain specific ...
8   METHODS\tSecondary outcomes include : depressi...
9   METHODS\tData collection will take place at ba...
10  CONCLUSIONS\tResults of the Positive Outlook s...
11                  BACKGROUND\tACTRN12612000642886 .
12                                        ###20497432

In [57]:

df = pd.DataFrame(columns=['id', 'content'])
count = 0
content = ""
id = ""
for i in tqdm(range(len(data[0]))):
  row = data[0][i]
  if '###' in row:
    id = row.split('###')[1]
    content = ""
  else:
    row = row.replace("\t"," ")
    row = row.split(' ')[1:]
    row1 = ''
    for word in row:
      row1 = row1 + " " + word
    content += row1

    if i == len(data[0]) - 1 or '###' in data[0][i+1]:
      output = {
          "id": id,
          "contents": content
      }

      # df.loc[0] = { "id": id, 'content': content }
      # result = df.to_json(orient="records")
      # parsed = json.loads(result)
      with open('tests/resources/'+ str(id) +'.json', "w") as t:
          json.dump(output, t)
      count += 1



100%|██████████| 2106393/2106393 [01:06<00:00, 31512.06it/s]


In [58]:
# result = df.to_json(orient="records")
# parsed = json.loads(result)
# with open('data.json', "w") as t:
#     json.dump(parsed, t)

In [59]:
!python -m pyserini.index.lucene \
  --collection JsonCollection \
  --input tests/resources \
  --index indexes/sample_collection_jsonl \
  --generator DefaultLuceneDocumentGenerator \
  --threads 1 \
  --storePositions --storeDocvectors --storeRaw

串流輸出內容已截斷至最後 5000 行。
2024-03-19 06:05:53,778 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/8427842.json: 1 docs added.
2024-03-19 06:05:53,778 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/22114896.json: 1 docs added.
2024-03-19 06:05:53,778 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/8033487.json: 1 docs added.
2024-03-19 06:05:53,779 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/14676650.json: 1 docs added.
2024-03-19 06:05:53,779 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/24359938.json: 1 docs added.
2024-03-19 06:05:53,779 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/22805468.json: 1 docs added.
2024-03-19 06:05:53,779 DEBUG [pool-2-thread-1] index.AbstractIndexer

In [60]:
!pip install faiss-cpu

In [61]:
from pyserini.search.lucene import LuceneSearcher
import time
searcher = LuceneSearcher('indexes/sample_collection_jsonl')

start = time.time()
hits = searcher.search('cancer',  k=300000)
print(hits)
end = time.time()

for i in range(len(hits)):
    filename = '/content/tests/resources/'+str(hits[i].docid)+'.json'
    f = open (filename, "r")

    data = json.loads(f.read())
    print(f'{i+1:2} {hits[i].docid:4} {hits[i].score:.5f} \n {data}')


print("執行時間：%f 秒" % (end - start))

[<io.anserini.search.ScoredDoc at 0x7db12b956a70 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b280 at 0x7db12f389370>>, <io.anserini.search.ScoredDoc at 0x7db12b956070 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b288 at 0x7db12f8417d0>>, <io.anserini.search.ScoredDoc at 0x7db12b957330 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b290 at 0x7db12f841c50>>, <io.anserini.search.ScoredDoc at 0x7db12b956390 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b298 at 0x7db12f841c70>>, <io.anserini.search.ScoredDoc at 0x7db12b955170 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b2a0 at 0x7db12f841c10>>, <io.anserini.search.ScoredDoc at 0x7db12b954680 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b2a8 at 0x7db12f389c90>>, <io.anserini.search.ScoredDoc at 0x7db12b957fb0 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x58612ed7b2b0 at 0x7db12f841650>>, <io.anserini.search

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



8789 10924844 1.40778 
 {'id': '10924844', 'contents': ' Because estrogens stimulate the synthesis and release of leptin in the adipocytes , the effect of antiestrogens on the circulating leptin levels were studied . Thirty postmenopausal patients with breast cancer were randomized to start either with tamoxifen ( 20 mg/day , n = 15 ) or toremifene ( 40 mg/day , n = 15 ) , and the patients were examined and serum leptin concentrations measured before the study and at 6 and 12 months . The baseline leptin concentrations ranged from 4.4 to 60.0 microg/l ( 15.3 + / -13.1 microg/l , mean + / - S.D. ) , and it correlated positively with the body mass index ( BMI ) of the subjects ( r = 0.73 , P = 0.0001 ) . Taking as a whole the antiestrogen regimen was associated with elevated leptin levels at 6 months ( 19.5 + / -13.8 microg/l , P = 0.0001 ) but no excess increase in leptin levels were seen at 12 months ( 20.9 + / -13.5 microg/l , NS ) . Subgroup analysis showed no difference between the 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [62]:
print("執行時間：%f 秒" % (end - start))

執行時間：0.761963 秒


In [63]:
import glob

searchKey = 'cancer'
list = []
start = time.time()

all_file = glob.glob('/content/tests/resources/*.json')

for filename in all_file:
  with open(filename, 'r') as f:
      json_data = json.load(f)
      json_data['contents']
      if searchKey in json_data['contents']:
          list.append(json_data)
end = time.time()


In [64]:
print("執行時間：%f 秒" % (end - start))

執行時間：6.977457 秒


##### 用Inverted index 來搜尋的時間為 0.761963 秒 , 用暴力搜尋法的時間為 6.977457 秒， 速度上inverted index 快了至少8倍